In [0]:
cb = spark.table("safegraph.censusblock_table")
cbg = spark.table("safegraph.censusblockgroup_pkmap")
patterns = spark.table("safegraph.patterns")
places = spark.table("safegraph.places")
census_mapping_safe_graph = spark.table("safegraph.censusmapping")
census_tract_pk_map=spark.table('safegraph.censustract_pkmap')

tract_members = spark.table("membership.tract_membership")
tract_member_info = spark.table("membership.tract_membership_populations")

tract_spatial = spark.table("census.tract_spatial")
tract_nearest = spark.table("census.tract_distance_to_nearest_temple")

temples= spark.table("chapel.temple_scrape")
tract_temple_distance = spark.table("chapel.tract_temple_distance")

# Easy Feature

In [0]:
for df in [cb, cbg, patterns, places, census_mapping_safe_graph, tract_members, tract_member_info, tract_spatial, census_tract_pk_map, tract_nearest, temples, tract_temple_distance]:
    df.printSchema()
    df.show(5)

root
 |-- state: string (nullable = true)
 |-- county: string (nullable = true)
 |-- tract: string (nullable = true)
 |-- name: string (nullable = true)
 |-- land_m: double (nullable = true)
 |-- blockcode: string (nullable = true)
 |-- water_m: double (nullable = true)
 |-- lat: double (nullable = true)
 |-- long: double (nullable = true)
 |-- cnamelong: string (nullable = true)
 |-- tractname: string (nullable = true)
 |-- tractcode: string (nullable = true)
 |-- stusab: string (nullable = true)
 |-- state_name: string (nullable = true)
 |-- statens: string (nullable = true)

+-----+------+------+-------------+-----------+------------+-----------+----------+-----------+---------------+---------+-----------+------+----------+--------+
|state|county| tract|         name|     land_m|   blockcode|    water_m|       lat|       long|      cnamelong|tractname|  tractcode|stusab|state_name| statens|
+-----+------+------+-------------+-----------+------------+-----------+----------+----------

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.functions import udf, avg, col
from pyspark.sql.types import DoubleType
import plotly.express as px

In [0]:
unique_temples= temples.select('temple').distinct()
usa_temples = unique_temples.filter(F.col('country')== "United States")


temple Albuquerque New Mexico Temple Anchorage Alaska Temple Atlanta Georgia Temple Austin Texas Temple Bakersfield California Temple Baton Rouge Louisiana Temple Bentonville Arkansas Temple Billings Montana Temple Birmingham Alabama Temple Bismarck North Dakota Temple Boise Idaho Temple Boston Massachusetts Temple Bountiful Utah Temple Brigham City Utah Temple Burley Idaho Temple Casper Wyoming Temple Cedar City Utah Temple Charlotte North Carolina Temple Chicago Illinois Temple Cleveland Ohio Temple Cody Wyoming Temple Columbia River Washington Temple Columbia South Carolina Temple Columbus Ohio Temple Dallas Texas Temple Denver Colorado Temple Deseret Peak Utah Temple Detroit Michigan Temple Draper Utah Temple Elko Nevada Temple Ephraim Utah Temple Farmington New Mexico Temple Feather River California Temple Fort Collins Colorado Temple Fort Lauderdale Florida Temple Fort Worth Texas Temple Fresno California Temple Gilbert Arizona Temple Grand Junction Colorado Temple Grand Rapids Michigan Temple Hartford Connecticut Temple Heber Valley Utah Temple Helena Montana Temple Houston Texas Temple Idaho Falls Idaho Temple Indianapolis Indiana Temple Jordan River Utah Temple Kansas City Missouri Temple Knoxville Tennessee Temple Kona Hawaii Temple Laie Hawaii Temple Las Vegas Nevada Temple Layton Utah Temple Lindon Utah Temple Logan Utah Temple Lone Mountain Nevada Temple Los Angeles California Temple Louisville Kentucky Temple Lubbock Texas Temple Manhattan New York Temple Manti Utah Temple McAllen Texas Temple Medford Oregon Temple Memphis Tennessee Temple Meridian Idaho Temple Mesa Arizona Temple Modesto California Temple Monticello Utah Temple Montpelier Idaho Temple Moses Lake Washington Temple Mount Timpanogos Utah Temple Nashville Tennessee Temple Nauvoo Illinois Temple Newport Beach California Temple Oakland California Temple Ogden Utah Temple Oklahoma City Oklahoma Temple Oquirrh Mountain Utah Temple Orem Utah Temple Orlando Florida Temple Palmyra New York Temple Payson Utah Temple Philadelphia Pennsylvania Temple Phoenix Arizona Temple Pittsburgh Pennsylvania Temple Pocatello Idaho Temple Portland Oregon Temple Provo City Center Temple Provo Utah Temple Raleigh North Carolina Temple Red Cliffs Utah Temple Redlands California Temple Reno Nevada Temple Rexburg Idaho Temple Richmond Virginia Temple Sacramento California Temple Salt Lake Temple San Antonio Texas Temple San Diego California Temple San Jose California Temple Saratoga Springs Utah Temple Seattle Washington Temple Smithfield Utah Temple Snowflake Arizona Temple Spokane Washington Temple St. George Utah Temple St. Louis Missouri Temple St. Paul Minnesota Temple Star Valley Wyoming Temple Syracuse Utah Temple Tallahassee Florida Temple Tampa Florida Temple Taylorsville Utah Temple Teton River Idaho Temple The Gila Valley Arizona Temple Tucson Arizona Temple Twin Falls Idaho Temple Vernal Utah Temple Washington D.C. Temple Wichita Kansas Temple Willamette Valley Oregon Temple Winter Quarters Nebraska Temple Yorba Linda California Temple

In [0]:
joined_tract_data = tract_member_info.join(tract_nearest, tract_member_info["home"] == tract_nearest["tract"])

In [0]:
joined_tract_data = joined_tract_data.withColumn("temple_accessibility_index", F.col("active_members_estimate") / (F.col("meters") + 1))

In [0]:

joined_tract_data = joined_tract_data.drop("name")



In [0]:
temples_with_tract_distance = tract_temple_distance.join(
    joined_tract_data,
    tract_temple_distance["tract"] == joined_tract_data["home"]
)



In [0]:
final_data = temples.join(
    temples_with_tract_distance,
    temples_with_tract_distance["name"] == temples["templeNameId"]
)

In [0]:
visualization_data = final_data.select(
    'lat_general',
    'long_general',
    'temple_accessibility_index',
    'temple',
    'templeNameId',
    'stateRegion',
    'active_members_estimate'
).dropDuplicates(['templeNameId'])



In [0]:

pandas_df = visualization_data.toPandas()

In [0]:

fig = px.scatter_mapbox(pandas_df, lat="lat_general", lon="long_general", 
                        color="temple_accessibility_index",
                        size="active_members_estimate",
                        color_continuous_scale=px.colors.cyclical.IceFire,
                        zoom=4, height=700)

fig.update_layout(mapbox_style="open-street-map")
fig.show()

The 'temple_accessibility_index' tells us a simple, human story: it shows how close people are to their community temples. With each tract measured, we can see which neighborhoods have easy access and which might be feeling a bit left out. It's a handy measure that could help figure out the best spots to build new temples so that more people can get to their place of peace without a long trek.

# Complex Feature

In [0]:
lds_church = places.filter(
    (F.col("top_category") == "Religious Organizations") &
    (F.col("location_name").rlike("Latter|latter|Saints|saints|LDS|\b[Ww]ard\b")) &
    (F.col("location_name").rlike("^((?!Reorganized).)*$")) &
    (F.col("location_name").rlike("^((?!All Saints).)*$")) &
    (F.col("location_name").rlike("^((?![cC]ath).)*$")) &
    (F.col("location_name").rlike("^((?![Bb]ody).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]eter).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]atholic).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]res).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]inist).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]ission).)*$")) &
    (F.col("location_name").rlike("^((?![Ww]orship).)*$")) &
    (F.col("location_name").rlike("^((?![Rr]ain).)*$")) &
    (F.col("location_name").rlike("^((?![Bb]aptist).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]eth).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]vang).)*$")) &
    (F.col("location_name").rlike("^((?![Ll]utheran).)*$")) &
    (F.col("location_name").rlike("^((?![Oo]rthodox).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]piscopal).)*$")) &
    (F.col("location_name").rlike("^((?![Tt]abernacle).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]arvest).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]ssem).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]edia).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]artha).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]hristian).)*$")) &
    (F.col("location_name").rlike("^((?![Uu]nited).)*$")) &
    (F.col("location_name").rlike("^((?![Ff]ellowship).)*$")) &
    (F.col("location_name").rlike("^((?![Ww]esl).)*$")) &
    (F.col("location_name").rlike("^((?![C]cosmas).)*$")) &
    (F.col("location_name").rlike("^((?![Gg]reater).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]rison).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]ommuni).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]lement).)*$")) &
    (F.col("location_name").rlike("^((?![Vv]iridian).)*$")) &
    (F.col("location_name").rlike("^((?![Dd]iocese).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]istory).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]chool).)*$")) &
    (F.col("location_name").rlike("^((?![Tt]hougt).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]oliness).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]artyr).)*$")) &
    (F.col("location_name").rlike("^((?![Jj]ames).)*$")) &
    (F.col("location_name").rlike("^((?![Ff]ellowship).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]ouse).)*$")) &
    (F.col("location_name").rlike("^((?![Gg]lory).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]nglican).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]oetic).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]anctuary).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]quipping).)*$")) &
    (F.col("location_name").rlike("^((?![Jj]ohn).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]ndrew).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]manuel).)*$")) &
    (F.col("location_name").rlike("^((?![Rr]edeemed).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]erfecting).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]ngel).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]rchangel).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]icheal).)*$")) &
    (F.col("location_name").rlike("^((?![Tt]hought).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]ariosse).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]osmas).)*$")) &
    (F.col("location_name").rlike("^((?![Dd]eliverance).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]ociete).)*$")) &
    (F.col("location_name").rlike("^((?![Tt]emple).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]eminary).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]mployment).)*$")) &
    (F.col("location_name").rlike("^((?![Ii]nstitute).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]amp).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]tudent).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]ducation).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]ocial).)*$")) &
    (F.col("location_name").rlike("^((?![Ww]welfare).)*$")) &
    (F.col("location_name").rlike("^((?![Cc][Ee][Ss]).)*$")) &
    (F.col("location_name").rlike("^((?![Ff]amily).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]ary).)*$")) &
    (F.col("location_name").rlike("^((?![Rr]ussian).)*$")) &
    (F.col("location_name").rlike("^((?![Bb]eautif).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]eaven).)*$")) &    
    (F.col("location_name").rlike("^((?!Inc).)*$")) &
    (F.col("location_name").rlike("^((?!God).)*$"))
  )

lds_places = lds_church.dropDuplicates(['placekey'])

In [0]:
patterns_linked = (
    patterns
    .join(places, patterns["placekey"] == lds_places["placekey"])
    .filter(places["iso_country_code"] == "US")  
    .dropDuplicates(["placekey"])
    .select(
        patterns["*"], 
        places["location_name"], 
        places["brands"], 
        places["top_category"], 
        places["sub_category"], 
        places["naics_code"], 
        places["city"], 
        places["region"],
        places["iso_country_code"]
    )
)


In [0]:
patterns_linked_agg = patterns_linked.groupBy('placekey').agg(
    F.sum('raw_visit_counts').alias('total_visits'),
    F.sum('raw_visitor_counts').alias('total_visitors')
)


In [0]:
pattern_link_exclude = ["date_range_start", "date_range_end", "bucketed_dwell_times", "related_same_day_brand", "related_same_month_brand", "device_type", "visitor_home_cbgs", "visitor_daytime_cbgs", "visitor_home_aggregration", "visitor_country_of_origin","popularity_by_hour", "popularity_by_day", "visits_by_day", "visitor_home_aggregation"]

In [0]:
census_tract_columns = [col(c) for c in census_tract_pk_map.columns if c != "placekey"]
census_tract_pk_map = census_tract_pk_map.withColumnRenamed("placekey", "census_placekey")

pattern_link_include_columns = [col(c) for c in patterns_linked_agg.columns if c not in pattern_link_exclude]

patterns_linked_with_tract = (
    patterns_linked_agg
    .join(census_tract_pk_map, census_tract_pk_map["census_placekey"] == patterns_linked_agg["placekey"])
    .dropDuplicates(["placekey"])
    .select(*pattern_link_include_columns, *census_tract_columns)
)

In [0]:
patterns_linked_with_tract_member_info = (
    patterns_linked_with_tract
        .join(tract_member_info, tract_member_info["home"] == patterns_linked_with_tract["tractcode"])
)

In [0]:
engagement_index = patterns_linked_with_tract_member_info.groupBy('tractcode').agg(
    F.sum('active_members_estimate').alias('total_active_members'),
    F.sum('total_visits').alias('sum_visits'),
    F.sum('total_visitors').alias('sum_visitors')
).withColumn('lds_community_engagement_index', 
             (F.col('total_active_members') + F.col('sum_visits') + F.col('sum_visitors')) / 3)  


In [0]:
from pyspark.sql.window import Window


In [0]:

# Normalize distance to nearest temple
w = Window.partitionBy()
normalized_distance = tract_nearest.withColumn('normalized_distance', 
                                                       (F.col('miles') - F.min('miles').over(w)) / (F.max('miles').over(w) - F.min('miles').over(w)))



In [0]:

combined_data = engagement_index.join(normalized_distance, normalized_distance["tract"] == engagement_index["tractcode"])


combined_data = combined_data.join(tract_member_info, combined_data['tract'] == tract_member_info['home'])

# Calculate Temple Suitability Score
combined_data = combined_data.withColumn('temple_suitability_score', 
                                         (F.col('normalized_distance') + F.col('population') + F.col('lds_community_engagement_index')) / 3)
combined_data = combined_data.dropDuplicates(["tractcode"])

In [0]:

windowSpec = Window.orderBy(F.lit(1))  # Window specification for unpartitioned DataFrame

# Normalize the LDS Community Engagement Index
combined_data = combined_data.withColumn(
    'normalized_lds_index', 
    (F.col('lds_community_engagement_index') - F.min('lds_community_engagement_index').over(windowSpec)) / 
    (F.max('lds_community_engagement_index').over(windowSpec) - F.min('lds_community_engagement_index').over(windowSpec))
)

# Normalize the Temple Suitability Score
combined_data = combined_data.withColumn(
    'normalized_temple_suitability_score', 
    (F.col('temple_suitability_score') - F.min('temple_suitability_score').over(windowSpec)) / 
    (F.max('temple_suitability_score').over(windowSpec) - F.min('temple_suitability_score').over(windowSpec))
)

final_data_complex = combined_data.select(
    'tractcode', 'normalized_lds_index', 'normalized_temple_suitability_score'
)

final_data_complex = final_data_complex.dropDuplicates(["tractcode"])

In [0]:
plot_df = final_data_complex.select('tractcode', 'normalized_lds_index', 'normalized_temple_suitability_score').toPandas()


In [0]:

fig = px.scatter(plot_df, x='normalized_lds_index', y='normalized_temple_suitability_score', 
                 hover_data=['tractcode'], title='LDS Community Engagement Index vs Temple Suitability Score')
fig.show()

The scatter plot displays a positive correlation between the Normalized LDS Community Engagement Index and the Normalized Temple Suitability Score, suggesting that tracts with higher engagement levels tend to be more suitable for temple placement. Most data points are clustered towards the lower end of both indices, indicating that both higher engagement and higher suitability are less common across tracts. A few outliers, particularly at higher engagement levels, may represent unique areas with specific characteristics that could be prime candidates for temple placement or could signal data points that warrant further investigation. The plot also reveals that while there is a general trend of increasing suitability with increasing engagement, the relationship is not strictly linear, suggesting that factors other than engagement could significantly influence temple suitability.